In [ ]:
#| echo: false
## PAQUETES

import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')

from datetime import datetime
import requests
import seaborn as sns
sns.set()
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
plt.rcParams['axes.labelsize'] = 10
plt.rcParams['xtick.labelsize'] = 10
plt.rcParams['ytick.labelsize'] = 10

import re

# IQR/Z score.
from scipy.stats import stats

# Seleción de variables.
from sklearn.feature_selection import SelectKBest

# Modelos Selección.
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV, StratifiedKFold

# Modelos.
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import LinearSVC
from xgboost import XGBClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import AdaBoostClassifier
from sklearn.linear_model import LassoCV
from sklearn.linear_model import RidgeClassifierCV
from sklearn.svm import SVC
from sklearn.model_selection import RepeatedStratifiedKFold

# Preprocesado.
from sklearn.preprocessing import MinMaxScaler

from imblearn.over_sampling import SMOTE
import pickle

# Métricas.
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score, auc, confusion_matrix, f1_score, precision_score, recall_score, roc_curve, classification_report

Finalmente, y también a modo ilustrativo, se realizó una caracterización socioeconómica y geográfica de los hogares. Para presentar los resultados obtenidos se muestra el mapa de Uruguay por departamentos, y barrios para el caso de Montevideo (capital del país), empleando las predicciones de ingreso obtenidas con el algoritmo obtenido. De él se desprende como los hogares con mayor ingreso per cápita en Uruguay se ubica en el departamento de Montevideo, y dentro de este, en los barrios costeros de Carrasco, Punta Gorda, Pocitos y Punta Carretas lo cual resulta consistente con la teoría al respecto.[^4]

[^4]: [Mapas vectoriales de uruguay](https://www.gub.uy/instituto-nacional-estadistica/datos-y-estadisticas/estadisticas/mapas-vectoriales-ano-2011)


In [ ]:
#| echo: false

# Separar features y target
#X_tst = df_test.drop(['l_ypc'], axis=1)
#y_tst = df_test['l_ypc']

X_tst.info(verbose=True)

In [ ]:
#| echo: false

import pandas as pd
import re


# Extraigo las columnas que coinciden con el patrón 'Departamento_o_Barrio'
columnas = [col for col in X_tst.columns if col.startswith('Departamento_o_Barrio')]

# Nueva columna vacía para almacenar la variable reconstruida
X_tst['Departamento_o_Barrio_reconstruido'] = 0

for col in columnas:
    # Identifico si la columna pertenece al patrón 'Departamento_o_Barrio_1_XX' o 'Departamento_o_Barrio_XX'
    if '_1_' in col:
        # Caso del patrón 'Departamento_o_Barrio_1_XX'
        depto_barrio = re.findall(r'1_(\d+)', col)[-1]  # Extraer el número del barrio después de '1_'
        depto_barrio = f"1_{depto_barrio}"  # Combinar departamento 1 con el número del barrio
    else:
        # Caso del patrón 'Departamento_o_Barrio_XX'
        depto_barrio = re.findall(r'(\d+)', col)[-1]  # Extraer el último número, que es el departamento
        depto_barrio = depto_barrio  # Es solo el número del departamento

    # Asignar el número de departamento o barrio cuando la variable binaria sea 1
    X_tst['Departamento_o_Barrio_reconstruido'] = X_tst.apply(
        lambda row: depto_barrio if row[col] == 1 else row['Departamento_o_Barrio_reconstruido'],
        axis=1
    )

X_tst[['Departamento_o_Barrio_reconstruido']].head()


In [ ]:
#| echo: false

pd.set_option('display.max_rows', None)
X_tst['Departamento_o_Barrio_reconstruido'].value_counts(dropna=False)


In [ ]:
#| echo: false

# controlo que quedo bien la variable reconstruida

pd.set_option('display.max_rows', None)

# Filtro el DataFrame por anio == 2023 y mostrar el conteo de 'Departamento_o_Barrio'
df_hog[df_hog['anio'] == 2023]['Departamento_o_Barrio'].value_counts(dropna=False)



In [ ]:
#| echo: false

df_predicciones = pd.DataFrame({
    'ID': X_tst.index,  # Usar el índice 'ID'
    'GB_pred_tst': GB_pred_tst
})

X_tst = X_tst.merge(df_predicciones, left_index=True, right_on='ID', how='left')

X_tst.head()

# Agrupo por 'Departamento_o_Barrio_reconstruido' y calculo mediana
median_pred_by_departamento = X_tst.groupby('Departamento_o_Barrio_reconstruido')['GB_pred_tst'].median()
median_pred_by_departamento


In [ ]:
#| echo: false

import numpy as np

# Calculo el valor original del ingreso a partir del logaritmo
X_tst['Ingreso_original'] = np.exp(X_tst['GB_pred_tst'])
X_tst[['GB_pred_tst', 'Ingreso_original']].head()



In [ ]:
#| echo: false

# Agrupo por 'Departamento_o_Barrio_reconstruido' y calcular la mediana de 'GB_pred_tst'
median_pred_by_dep_exp = X_tst.groupby('Departamento_o_Barrio_reconstruido')['Ingreso_original'].median().round(2)

In [ ]:
#| echo: false

import geopandas as gpd

# Cargo el shapefile
ruta = "/Users/mariadolorescarnevale/Desktop/Maestria data science/TFM/ine_depto.shp"
gdf = gpd.read_file(ruta)
print(gdf.head())

In [ ]:
#| echo: false

# Asigno un CRS
gdf = gdf.set_crs(epsg=32721)
# Reproyectar a WGS 84 (latitud/longitud)
gdf = gdf.to_crs(epsg=4326)

In [ ]:
#| echo: false

import geopandas as gpd

# Cargo el shapefile
ruta = "/Users/mariadolorescarnevale/Desktop/Maestria data science/TFM/ine_barrios_mvd_nbi85.shp"
gdf_mvd = gpd.read_file(ruta)
print(gdf_mvd.head())

In [ ]:
#| echo: false

# Asigno un CRS
gdf_mvd = gdf_mvd.set_crs(epsg=32721)  # UTM Zone 21S para Uruguay

# Reproyectar a WGS 84 (latitud/longitud)
gdf_mvd = gdf_mvd.to_crs(epsg=4326)

In [ ]:
#| echo: false

# Filtro gdf para DEPTO == 1
gdf_depto = gdf[gdf['DEPTO'] != 1].copy()

# Creo la nueva variable en gdf_depto1
gdf_depto['Departamento_o_Barrio_reconstruido'] = gdf_depto['DEPTO'].astype(str)

In [ ]:
#| echo: false

# Creo la nueva variable en gdf_mvd
gdf_mvd['Departamento_o_Barrio_reconstruido'] = '1_' + gdf_mvd['NROBARRIO'].astype(str)


In [ ]:
#| echo: false

import pandas as pd

# uno bases
gdf_combined = pd.concat([gdf_depto, gdf_mvd], ignore_index=True)
gdf_combined.head()

In [ ]:
#| echo: false

gdf_combined = gdf_combined.merge(median_pred_by_dep_exp, on='Departamento_o_Barrio_reconstruido', how='left')


In [ ]:
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
import numpy as np
import folium
import branca.colormap as cm

# 'Ingreso_original'
min_ingreso = gdf_combined['Ingreso_original'].min()
max_ingreso = gdf_combined['Ingreso_original'].max()

norm = plt.Normalize(vmin=min_ingreso, vmax=max_ingreso)
colors = plt.cm.RdYlBu(norm(gdf_combined['Ingreso_original']))

color_dict = {name: mcolors.to_hex(color) for name, color in zip(gdf_combined['Departamento_o_Barrio_reconstruido'], colors)}

colormap = cm.LinearColormap(
    colors=['#d73027', '#ffffbf', '#4575b4'],
    vmin=min_ingreso,
    vmax=max_ingreso,
    caption='Ingreso Original'
)

# Crear un mapa centrado en el centro geográfico de los datos
m = folium.Map(location=[gdf_combined.geometry.centroid.y.mean(), gdf_combined.geometry.centroid.x.mean()], zoom_start=10)

folium.GeoJson(
    gdf_combined,
    name="Barrios y Departamentos",
    style_function=lambda feature: {
        'fillColor': color_dict[feature['properties']['Departamento_o_Barrio_reconstruido']],
        'color': 'black',
        'weight': 0.5,
        'fillOpacity': 0.5,
    },
    tooltip=folium.GeoJsonTooltip(fields=['Departamento_o_Barrio_reconstruido', 'Ingreso_original'])
).add_to(m)

# Añado la barra de colores al mapa
colormap.add_to(m)

m.save("mapa_reconstruido_ingreso.html")
m



# Conclusiones


